# Pipeline to reproduce figures for rt-me-fMRI methods article

Sections:

1. [Imports]()
2. []()
3. []()
4. []()
5. []()
6. []()
7. []()
8. []()

RFX = results figure X. Figures are numbered relative to the results section, starting at RF1.

## 1. Imports

In [1]:
%load_ext autoreload
%autoreload 2
import sys
sys.path.append("python")
from jupyter_dash import JupyterDash
import dash
import dash_core_components as dcc
import dash_html_components as html
import dash_bootstrap_components as dbc
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import shutil
import glob
import os
import math
from IPython.display import display, set_matplotlib_formats
import nibabel as nib
from nilearn import plotting
from nilearn.image import load_img
from dash.dependencies import Input, Output
from dash.exceptions import PreventUpdate
from plotly.colors import sequential, n_colors
import plotly.graph_objs as go
from bids import BIDSLayout
from nilearn.image.image import mean_img
import utilities as util

/Users/jheunis/miniconda3/envs/rtme-fmri/lib/python3.7/site-packages/sklearn/externals/joblib/__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


## 2. RF1-RF3: Image intensity and tSNR to show decay, dropout and recovery

This includes montages of:

- Single volumes of echos to show decay (RF1)
- Image intensity volumes from all six timeseries to show dropout and signal recovery (RF2)
- tSNR volumes from of all six timeseries to show dropout and signal recovery (RF3)

All of these are generated by the Matlab script `rtme_reproduce_methodsFigures`.

This requires access to the preprocessed data of the rt-me-fMRI dataset.

## 3. RF4: tSNR distribution in grey matter for all time series, sub-001_task-rest_run-2

In [2]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
sub = 'sub-001'
task = 'rest_run-2'
ts_names = ['t2starFIT', 'combinedMEt2starFIT', 'combinedMEte', 'combinedMEt2star', 'combinedMEtsnr', 'echo-2']
ts_names_disp = ['T2*FIT', 'T2*FIT-combined', 'TE-combined', 'T2*-combined', 'tSNR-combined', 'Echo 2']

layout = go.Layout(
    yaxis = dict(title = 'Time series'),
    xaxis=dict(title='Temporal signal-to-noise ratio (tSNR) in Gray Matter', range=[-20, 300]),
    height = 600,
    margin={
          't': 10,
        })
fig_tsnr_persub = go.Figure(layout=layout)

data = []
for x, ts in enumerate(ts_names):
    if x == 5:
        GMtsnr_tsv = os.path.join(data_dir, 'multiecho', sub+'_task-'+task+'_echo-2_desc-rapreproc_GMtsnr.tsv')
    else:
        GMtsnr_tsv = os.path.join(data_dir, 'multiecho', sub+'_task-'+task+'_desc-' + ts + '_GMtsnr.tsv')

    df_GMtsnr = pd.read_csv(GMtsnr_tsv, sep='\t').dropna()
    new_dat = df_GMtsnr['tsnr'].to_numpy()
    if x == 0:
        new_dat[new_dat < 0] = math.nan
        new_dat[new_dat > 500] = math.nan
    
    data.append(new_dat)
    fig_tsnr_persub.add_trace(go.Violin(x=data[x], line_color=sequential.Inferno[8-x], name=ts_names_disp[x], points=False))

fig_tsnr_persub.update_traces(orientation='h', side='positive', width=2, box_visible=True, meanline_visible=True)
fig_tsnr_persub.update_layout(xaxis_showgrid=True, yaxis_showgrid=True, xaxis_zeroline=False, legend={'traceorder':'reversed'})

## 4. RF5: Mean grey matter tSNR distributions over all subjects and all runs

In [3]:
layout = go.Layout(
        yaxis = dict(title = 'Mean tSNR in gray matter', range=[0, 250]),
        xaxis = dict(title='Time series'),
        margin = {
              't': 10,
            })
tsnr_regions = ['whole brain', 'lmotor', 'bamygdala']
fig_tsnr_mean = [None, None, None]
tsnr_runs = ['all runs', 'fingerTapping', 'emotionProcessing', 'rest_run-2', 'fingerTappingImagined', 'emotionProcessingImagined']
tsnr_run = tsnr_runs[0]
for i, region in enumerate(tsnr_regions):
    fig_tsnr_mean[i] = util.reset_tsnr_summary(go.Figure(layout=layout), data_dir, region, tsnr_run)

In [4]:
# RF5-A
fig_tsnr_mean[0]

In [5]:
# RF5-B
fig_tsnr_mean[1]

In [6]:
# RF5-C
fig_tsnr_mean[2]

## PSC

# RF6

In [26]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
        yaxis = dict(title = 'Precentage signal change', range=[0, 3.25]), # 
        xaxis = dict(title='Time series'),
        margin = {
              't': 10,
            })

fig_psc_summary = [None, None, None, None]
tasks = ['fingerTapping', 'fingerTappingImagined', 'emotionProcessing', 'emotionProcessingImagined']
summary_opt = 'mean'
cluster_opts = ['FWE', 'fweOR', 'anatROI']
cluster_opt = cluster_opts[1]
for i, task in enumerate(tasks):
    fig_psc_summary[i] = util.reset_psc_summary_img(go.Figure(layout=layout), data_dir, task, summary_opt, cluster_opt)

In [27]:
# RF6A
fig_psc_summary[0]

In [28]:
# RF6B
fig_psc_summary[1]

In [29]:
# RF6C
fig_psc_summary[2]

In [30]:
# RF6D
fig_psc_summary[3]

In [31]:
#RF7A-H: not sure if this will eventually be plotted. Leaving out for now.

# T-values - RF8ABC

In [36]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
    yaxis = dict(title = 'T-values', range=[0, 12]),
    xaxis = dict(title='Time series'),
    margin = {
          't': 10,
        })
fig_tvals_summary = [None, None, None]
task = 'fingerTapping'
summary_opt = 'mean'
cluster_opts = ['FWE', 'fweOR', 'anatROI']
for i, cluster_opt in enumerate(cluster_opts):
    fig_tvals_summary[i] = util.reset_tval_summary_img(go.Figure(layout=layout), data_dir, task, summary_opt, cluster_opt)


In [37]:
# RF8A
fig_tvals_summary[0]

In [38]:
# RF8B
fig_tvals_summary[1]

In [39]:
# RF8C
fig_tvals_summary[2]

# Offline tPCS and functional contrast - RF9ABC

In [42]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
    yaxis = dict(title = 'Percentage signal change', range=[-2.5, 2.5]),
    xaxis=dict(title='Time (functional volumes)'),
    margin={
          't': 10,
        })
fig_psc_timeseries = [None, None, None]
sub = 'sub-001'
task = 'fingerTapping'
cluster_opts = ['FWE', 'fweOR', 'anatROI']
for i, cluster_opt in enumerate(cluster_opts):
    fig_psc_timeseries[i] = util.reset_psc_timeseries_img(go.Figure(layout=layout), data_dir, sub, task, cluster_opt)


In [43]:
fig_psc_timeseries[0]

In [44]:
fig_psc_timeseries[1]

In [45]:
fig_psc_timeseries[2]

# Real-time contrast and tCNR

In [52]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data'
layout = go.Layout(
    xaxis = dict(title = 'Time series'),
    yaxis = dict(title='Percentage signal change', range=[-0.5, 3]),
    margin={
          't': 10,
        })
fig_realtime_summary = [None, None, None, None, None, None]

tasks = ['fingerTapping', 'emotionProcessing']
cnr_opt = 'cnr'
psc_types = ['glm', 'offline', 'cumulative', 'cumulativebas', 'previousbas']
psc_opt = psc_types[3]
clusters = [None, None]
clusters[0] = ['FWE', 'OR', 'rleftMotor']
clusters[1] = ['FWE', 'OR', 'rbilateralAmygdala']
i = 0
for t, task in enumerate(tasks):
    for c, cluster in enumerate(clusters[t]):
        fig_realtime_summary[i] = util.reset_realtime_summary_img(go.Figure(layout=layout), data_dir, cnr_opt, task, cluster, psc_opt)
        i+=1

In [53]:
fig_realtime_summary[0]

In [54]:
fig_realtime_summary[1]

In [55]:
fig_realtime_summary[2]

In [56]:
fig_realtime_summary[3]

In [57]:
fig_realtime_summary[4]

In [58]:
fig_realtime_summary[5]

In [62]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data'
layout = go.Layout(
    xaxis = dict(title = 'Time series'),
    yaxis = dict(title='Temporal contrast-to-noise ratio', range=[-0.5, 2]),
    margin={
          't': 10,
        })
fig_realtime_tcnr = [None, None]

tasks = ['fingerTapping', 'emotionProcessing']
cnr_opt = 'tcnr'
psc_types = ['glm', 'offline', 'cumulative', 'cumulativebas', 'previousbas']
psc_opt = psc_types[3]
cluster = 'OR'
for t, task in enumerate(tasks):
    fig_realtime_tcnr[t] = util.reset_realtime_summary_img(go.Figure(layout=layout), data_dir, cnr_opt, task, cluster, psc_opt)

In [63]:
fig_realtime_tcnr[0]

In [64]:
fig_realtime_tcnr[1]